In [1]:
import pandas as pd
import numpy as np
import altair as alt
from altair_saver import save

from datetime import timedelta, date
import time
from IPython.display import display, clear_output

alt.data_transformers.disable_max_rows()

df = pd.read_csv('./data-2021-01-18/CovidFaelle_Timeline_GKZ.csv', sep=';', decimal=",")
df['Time'] = pd.to_datetime(df['Time'], format='%d.%m.%Y %H:%M:%S')

df.SiebenTageInzidenzFaelle = df.SiebenTageInzidenzFaelle.round()
df['7TI'] = df['SiebenTageInzidenzFaelle']

df = df[["Time","Bezirk","7TI"]]

last_day = 17

df.head()

Time               Bezirk  7TI
0 2020-02-26    Eisenstadt(Stadt)  0.0
1 2020-02-26          Rust(Stadt)  0.0
2 2020-02-26  Eisenstadt-Umgebung  0.0
3 2020-02-26              Güssing  0.0
4 2020-02-26          Jennersdorf  0.0

In [2]:
df_all = pd.read_csv('./data-2021-01-18/CovidFaelle_Timeline.csv', sep=';', decimal=",")
df_all['Time'] = pd.to_datetime(df_all['Time'], format='%d.%m.%Y %H:%M:%S')

df_all.SiebenTageInzidenzFaelle = df_all.SiebenTageInzidenzFaelle.round()
df_all['7TI'] = df_all['SiebenTageInzidenzFaelle']

df_all = df_all[["Time","Bundesland","7TI"]]
df_all = df_all[df_all['Bundesland'] == 'Österreich']

df_all.head()

Time  Bundesland  7TI
9  2020-02-26  Österreich  0.0
19 2020-02-27  Österreich  0.0
29 2020-02-28  Österreich  0.0
39 2020-02-29  Österreich  0.0
49 2020-03-01  Österreich  0.0

In [3]:
bars_all = alt.Chart(df_all).mark_bar(align='left', dx=3, color='#5578a4').transform_timeunit(
    date='yearmonthdate(Time)'
).encode(
    x=alt.X('date:T'),
    y=alt.Y('7TI:Q')
).properties(
    width=480,
    height=100,
    title={
      "text": ["7-Tage-Inzidenz Österreich"], 
    }
)

bars_all

alt.Chart(...)

In [4]:
def last(df):
    return df.iloc[-1]

df_agg = df.groupby(['Bezirk']).apply(last).sort_values(by='7TI', ascending=False)
district_sorted_by_incidence = list(df_agg.index) 

In [5]:
search = ''

lines = alt.Chart(df).mark_line(
    strokeJoin='round'
).transform_timeunit(
    date='yearmonthdate(Time)'
).transform_filter(
    f'indexof(lower(datum.Bezirk), lower(\'{search}\')) >= 0'
).encode(
    alt.X('date:T', axis=None),
    alt.Y('7TI:Q', axis=None),
    alt.Tooltip(['date:T', '7TI:Q'])
).properties(
    width=120,
    height=40
)

labels = lines.mark_text(align='left', dx=3, color='#5578a4').transform_timeunit(
    date='yearmonthdate(Time)'
).encode(
    text=alt.Text('7TI:Q')
).transform_filter(
    f'indexof(lower(datum.Bezirk), lower(\'{search}\')) >= 0 & year(datum.date) >= 2021 & month(datum.date) >= 0 & date(datum.date) >= {last_day}'
)

(lines + labels).facet(
    alt.Facet('Bezirk:N', sort=district_sorted_by_incidence, header=alt.Header(
        labelAnchor='start',
        labelOrient='bottom',
        labelAlign='left',
        title=''
    )),
    columns=5
).configure_axis(
    grid=False
).configure_view(
    strokeOpacity=0
).properties(
    title={
      "text": ["7-Tage-Inzidenz pro Bezirk"], 
      "subtitle": [f'22.02.2020 - {last_day}.01.2021']
    }
)

alt.FacetChart(...)

In [6]:
bar_last_day = 17
top = 10

def bar_chart(the_date):
    bars_all = alt.Chart(df_all).mark_bar(align='left', dx=3, color='#5578a4').transform_timeunit(
        date='yearmonthdate(Time)'
    ).encode(
        x=alt.X('date:T', title=''),
        y=alt.Y('7TI:Q', title='')
    ).properties(
        width=480,
        height=100,
        title={
          "text": ["7-Tage-Inzidenz Österreich"], 
          "subtitle": [the_date.strftime("%d.%m.%Y")]
        }
    )
    
    rule = alt.Chart(df_all).transform_timeunit(
        date='yearmonthdate(Time)'
    ).mark_rule(color='red').encode(
        x='a:T'
    ).transform_filter(
        f'year(datum.date) == {the_date.year} & month(datum.date) == {the_date.month-1} & date(datum.date) == {the_date.day}'
    ).transform_timeunit(
        a='yearmonthdate(Time)'
    )
    
    bars_combo_all = bars_all + rule
  
    bars = alt.Chart(df).mark_bar(align='left', dx=3, color='#5578a4').transform_timeunit(
        date='yearmonthdate(Time)'
    ).encode(
        x=alt.X('7TI:Q', scale=alt.Scale(domain=[0, 1800]), title=''),
        y=alt.Y('Bezirk:N', sort='-x', scale=alt.Scale(padding=.2), title='')
    ).transform_filter(
        f'year(datum.date) == {the_date.year} & month(datum.date) == {the_date.month-1} & date(datum.date) == {the_date.day}'
    ).transform_window(
        rank='count(7TI)',
        sort=[alt.SortField('7TI', order='descending')]
    ).transform_filter(
        (alt.datum.rank <= top)
    ).transform_filter(
        (alt.datum['7TI'] > 0)
    ).properties(
        width=480,
        height=320,
        title={
          "text": ["7-Tage-Inzidenz Bezirke"]
        }
    )

    text = bars.mark_text(
        align='left',
        baseline='middle',
        dx=3,
        color='gray'
    ).encode(
        text='7TI:Q'
    )

    districts = bars + text
    
    return (bars_combo_all & districts).configure_axisY(
        minExtent=200, 
    )

single_date = date(2020, 4, 17)
chart = bar_chart(single_date)
# chart.save('img/chart.png')
chart

alt.VConcatChart(...)

In [7]:
def daterange(start_date, end_date):
    for n in range(int((end_date - start_date).days)):
        yield start_date + timedelta(n)

start_date = date(2020, 2, 26)
end_date = date(2021, 1, 17)
i = 0
for single_date in daterange(start_date, end_date):
    clear_output(wait=True)
#     display(bar_chart(single_date))
    chart = bar_chart(single_date)
    chart.save(f'img/bcr_{"{:04d}".format(i)}.png')
    i = i + 1
#     time.sleep(.1)

Error: Unrecognized transform type: "timeunit"
    at Object.error (/usr/local/anaconda3/lib/vega-cli/node_modules/vega-util/build/vega-util.js:22:11)
    at parseTransform (/usr/local/anaconda3/lib/vega-cli/node_modules/vega-parser/build/vega-parser.js:1635:24)
    at /usr/local/anaconda3/lib/vega-cli/node_modules/vega-parser/build/vega-parser.js:2413:25
    at Array.forEach (<anonymous>)
    at parseData$1 (/usr/local/anaconda3/lib/vega-cli/node_modules/vega-parser/build/vega-parser.js:2412:22)
    at vegaUtil.array.forEach._ (/usr/local/anaconda3/lib/vega-cli/node_modules/vega-parser/build/vega-parser.js:2951:44)
    at Array.forEach (<anonymous>)
    at parseSpec (/usr/local/anaconda3/lib/vega-cli/node_modules/vega-parser/build/vega-parser.js:2951:31)
    at parseView (/usr/local/anaconda3/lib/vega-cli/node_modules/vega-parser/build/vega-parser.js:3020:5)
    at Object.parse (/usr/local/anaconda3/lib/vega-cli/node_modules/vega-parser/build/vega-parser.js:3741:12)


In [8]:
# ffmpeg -y -i bcr_%04d.png -vf "scale=800:-1:flags=lanczos" -c:v pam -f image2pipe - | convert -delay 10 - -loop 0 -layers optimize output.gif


In [9]:
bar_last_day = 17
top = 10

def bar_chart(the_date):
    bars_all = alt.Chart(df_all).mark_bar(align='left', dx=3, color='#5578a4').transform_timeunit(
        date='yearmonthdate(Time)'
    ).encode(
        x=alt.X('date:T', title=''),
        y=alt.Y('7TI:Q', title='')
    ).properties(
        width=480,
        height=100,
        title={
          "text": ["7-Tage-Inzidenz Österreich"], 
          "subtitle": [the_date.strftime("%d.%m.%Y")]
        }
    )
    
    rule = alt.Chart(df_all).transform_timeunit(
        date='yearmonthdate(Time)'
    ).mark_rule(color='red').encode(
        x='a:T'
    ).transform_filter(
        f'year(datum.date) == {the_date.year} & month(datum.date) == {the_date.month-1} & date(datum.date) == {the_date.day}'
    ).transform_timeunit(
        a='yearmonthdate(Time)'
    )
    
    bars_combo_all = bars_all + rule
  
    bars = alt.Chart(df).mark_bar(align='left', dx=3, color='#5578a4').transform_timeunit(
        date='yearmonthdate(Time)'
    ).encode(
        x=alt.X('7TI:Q', scale=alt.Scale(domain=[0, 1800]), title=''),
        y=alt.Y('Bezirk:N', sort='-x', scale=alt.Scale(padding=.2), title='')
    ).transform_filter(
        f'year(datum.date) == {the_date.year} & month(datum.date) == {the_date.month-1} & date(datum.date) == {the_date.day}'
    ).transform_window(
        rank='count(7TI)',
        sort=[alt.SortField('7TI', order='descending')]
    ).transform_filter(
        (alt.datum.rank <= top)
    ).transform_filter(
        (alt.datum['7TI'] > 0)
    ).properties(
        width=480,
        height=320,
        title={
          "text": ["7-Tage-Inzidenz Bezirke"]
        }
    )

    text = bars.mark_text(
        align='left',
        baseline='middle',
        dx=3,
        color='gray'
    ).encode(
        text='7TI:Q'
    )

    districts = bars + text
    
    return (bars_combo_all & districts).configure_axisY(
        minExtent=200, 
    )

single_date = date(2021, 1, 17)
chart = bar_chart(single_date)
chart

alt.VConcatChart(...)